In [2]:
import pandas as pd
import matplotlib.pyplot as plt
from wordcloud import WordCloud
import numpy as np
import seaborn as sns
import copy
import time
import numpy as np
from sklearn.cluster import KMeans
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.metrics.pairwise import euclidean_distances
from sklearn.cluster import DBSCAN
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA
from sklearn.metrics import silhouette_score
import nltk
from sklearn.manifold import TSNE
from sklearn.feature_extraction.text import TfidfVectorizer
import string
from nltk.tokenize import RegexpTokenizer


In [4]:
# Загрузим модель, корпус слов и словарь
import gensim
from gensim import corpora

lda_model = gensim.models.LdaModel.load('lda_model.model')
dictionary = corpora.Dictionary.load('dictionary.dict')
corpus = gensim.corpora.MmCorpus('corpus.mm')

In [5]:
df = pd.read_csv('labelled_tickets.csv')

In [6]:
with pd.option_context('display.max_colwidth', None):
    display(df[df['topic'] == 1][['texts_cmb']])

texts_cmb
5                    ['уведомление', 'сбой', 'сторона', 'оператор', 'уважаемый', 'партнёр', 'мск', 'зафиксировать', 'сбой', 'сторона', 'мобильный', 'оператор', 'доставка', 'сообщение', 'абонент', 'данный', 'оператор', 'затруднить', 'мочь', 'осуществляться', 'задержка', 'данный', 'момент', 'доставка', 'осуществляться', 'штатный', 'режим', 'информация', 'оператор', 'причина', 'сбой', 'данный', 'момент', 'поступать', 'отдел', 'технический', 'поддержка', 'ао', 'загрузка']
13                                                                                                                                                                                                                                                                                                                                                  ['политика', 'обновление', 'ваш', 'пароль', 'доставка', 'сообщение', 'доставка', 'сообщение', 'диагностика', 'информация', 'сервер']
197    ['удаваться', 'доставить', 'политика', 'обновление', 'ваш', 'пароль', 'удаться', 'выполнить', 'доставка', 'следующий', 'получатель', 'группа', 'почтовый', 'ящик', 'получатель', 'заполнить', 'данный', 'момент', 'мочь', 'принимать', 'сообщение', 'попробовать', 'снова', 'отправить', 'письмо', 'поздний', 'обратиться', 'получатель', 'напрямую', 'организация', 'отклонить', 'сообщение', 'диагностический', 'сведение', 'администратор', 'формировать', 'сервер', 'сервер']
251                                                              ['уведомление', 'плановый', 'работа', 'оператор', 'тело', 'уважаемый', 'партнёр', 'сотовый', 'оператор', 'сообщать', 'необходимость', 'проведение', 'плановый', 'технический', 'работа', 'работа', 'проводиться', 'период', 'мскgmt', 'указанный', 'промежуток', 'мочь', 'наблюдаться', 'затруднение', 'доставка', 'сообщение', 'абонент', 'данный', 'оператор', 'отдел', 'технический', 'поддержка', 'ао', 'загрузка']
277                                                                                                                                                                                                                                                                                                                           ['политика', 'обновление', 'ваш', 'пароль', 'доставка', 'мэилбокс', 'сообщение', 'сообщение', 'диагностика', 'информация', 'сервер', 'сервер', 'мэилбокс']
...                                                                                                                                                                                                                                                                                                                                                                                                                                                                                  ...
10129                           ['уведомление', 'плановый', 'работа', 'оператор', 'мегафон', 'уважаемый', 'партнёр', 'сотовый', 'оператор', 'мегафон', 'сообщать', 'необходимость', 'проведение', 'плановый', 'технический', 'работа', 'работа', 'проводиться', 'период', 'мскgmt', 'указанный', 'промежуток', 'мочь', 'наблюдаться', 'затруднение', 'доставка', 'сообщение', 'абонент', 'данный', 'оператор', 'уважение', 'команда', 'круглосуточно', 'звонок', 'россия', 'бесплатный']
10131                                   ['уведомление', 'плановый', 'работа', 'оператор', 'мтс', 'уважаемый', 'партнёр', 'сотовый', 'оператор', 'мтс', 'сообщать', 'необходимость', 'проведение', 'плановый', 'технический', 'работа', 'работа', 'проводиться', 'период', 'мскgmt', 'указанный', 'промежуток', 'мочь', 'наблюдаться', 'затруднение', 'доставка', 'сообщение', 'абонент', 'данный', 'оператор', 'уважение', 'команда', 'круглосуточно', 'звонок', 'россия', 'бесплатный']
10135                                                ['уведомление', 'восстановление', 'сервис', 'отправка', 'сообщение', 'абонент', 'оператор', 'спринт', 'уважаемый', 'партнёр', 'фиксировать', 'восстановле

In [9]:
import pyLDAvis.gensim
import pyLDAvis.gensim_models as gensimvis

pyLDAvis.enable_notebook()  # Для Jupyter Notebook
vis = gensimvis.prepare(lda_model, corpus, dictionary)
pyLDAvis.display(vis)

# Темы для разметки

In [11]:
import warnings
warnings.simplefilter(action='ignore', category=DeprecationWarning)

```
1. Обращения
   1.1 Списания/денежные средства
   1.2 Проблемы с сим-меню
   1.3 Esim (проблемы подключения, код активации, qr-код)
   1.4 Проблемы с контентом и отключение услуг/ подписок/ сервисов
   1.5 Учетные записи
2. Информация
   2.6 Уведомления о технических работах
   2.7 Сбой работы (в работе оператора)
   2.8 Тесты, проблемы с доставкой, прочие тех. оповещения
3. Черный список
   3.9 Черный список
4. Спам
   4.10 Спам, реклама
```

Начнем с самых маленьких (и очевидных) кластеров. Для удобства разметки написала функцию, которая выводит срез датафрейма по условию и присваивает ему выбранный через виджет кластер

In [12]:
df['cluster'] = None

In [13]:
from ipywidgets import widgets

def assign_cluster(dataframe, column_name, include_keywords, exact_match=True, exclude_keywords=None):
    if isinstance(include_keywords, str):
        include_keywords = [include_keywords]
    include_pattern = '|'.join(include_keywords)

    if exact_match:
        filtered_df = dataframe[dataframe[column_name] == include_pattern]
    else:
        filtered_df = dataframe[dataframe[column_name].str.contains(include_pattern, case=False, na=False)]

    if exclude_keywords:
        if isinstance(exclude_keywords, str):
            exclude_keywords = [exclude_keywords]
        exclude_pattern = '|'.join(exclude_keywords)
        if exact_match:
            filtered_df = filtered_df[filtered_df[column_name] != exclude_pattern]
        else:
            filtered_df = filtered_df[~filtered_df[column_name].str.contains(exclude_pattern, case=False, na=False)]

    filtered_df = filtered_df[(filtered_df['texts_cmb'] != "[]") & (filtered_df['cluster'].isna())]
    filtered_df = filtered_df[['theme', 'topic', 'descr', 'sender_name']]

    pd.set_option('display.max_rows', None)
    pd.set_option('display.max_colwidth', None)
    display(filtered_df)
    pd.reset_option('display.max_rows')

    cluster_input = widgets.Dropdown(
        options=list(range(1, 11)),
        description="Номер кластера:",
        value=1
    )
    display(cluster_input)

    def click(b):
        cluster_num = cluster_input.value
        dataframe.loc[filtered_df.index, 'cluster'] = cluster_num

    button = widgets.Button(description="Присвоить кластер")
    button.on_click(click)
    display(button)

In [14]:
assign_cluster(df, 'theme', 'test')

theme  topic  \
35     test      8   
108    test      4   
145    test      8   
170    test      8   
5036   test      4   
5178   test      8   
5179   test      8   
5181   test      4   
7307   test      4   
9535   test      8   
9706   test      8   
9781   test      8   
9789   test      8   
9851   test      8   
9853   test      8   
9924   test      8   
10077  test      8   
10130  test      4   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                               descr  \
35           test C уважением, Фомиряков Степан Дежурный инженер СТПиЭ A1 Systems Моб.: +7 (900)-333-60-45 E-mail: s.fomiryakov@a1-systems.com Информация, содержащаяся в данном сообщении, является КОММЕРЧЕСКОЙ ТАЙНОЙ, и предназначена для строго определенного круга лиц. Если данное сообщение попало к Вам по ошибке, немедленно удалите его. Незаконное использование, копирование, распространение вышеуказанной информации влечет уголовную, административную, гражданск...   
108             test C уважением, Фомиряков Степан Дежурный инженер СТПиЭ A1 Systems Моб.: +7 (900)-333-60-45 E-mail: s.fomiryakov@a1-systems.com Информация, содержащаяся в данном сообщении, является КОММЕРЧЕСКОЙ ТАЙНОЙ, и предназначена для строго определенного круга лиц. Если данное сообщение попало к Вам по ошибке, немедленно удалите его. Незаконное использование, копирование, распространение вышеуказанной информации влечет уголовную, административную, гражда...   
145          test C уважением, Фомиряков Степан Дежурный инженер СТПиЭ A1 Systems Моб.: +7 (900)-333-60-45 E-mail: s.fomiryakov@a1-systems.com Информация, содержащаяся в данном сообщении, является КОММЕРЧЕСКОЙ ТАЙНОЙ, и предназначена для строго определенного круга лиц. Если данное сообщение попало к Вам по ошибке, немедленно удалите его. Незаконное использование, копирование, распространение вышеуказанной информации влечет уголовную, административную, гражданск...   
170        C уважением, Фролов Никита Дежурный инженер СТПиЭ A1 Systems Моб.: +7 (903)-210-81-98 E-mail: n.frolov@a1-systems.com Информация, содержащаяся в данном сообщении, является КОММЕРЧЕСКОЙ ТАЙНОЙ, и предназначена для строго определенного круга лиц. Если данное сообщение попало к Вам по ошибке, немедленно удалите его. Незаконное использование, копирование, распространение вышеуказанной информации влечет уголовную, административную, гражданско-правовую или...   
5036   test C уважением, Фролов Никита Дежурный инженер СТПиЭ A1 Systems Моб.: +7 (903)-210-81-98 E-mail: n.frolov@a1-systems.com Информация, содержащаяся в данном сообщении, является КОММЕРЧЕСКОЙ ТАЙНОЙ, и предназначена для строго определенного круга лиц. Если данное сообщение попало к Вам по ошибке, немедленно удалите его. Незаконное использование, копирование, распространение вышеуказанной информации влечет уголовную, административную, гражданско-правовую ил...   
5178      test C уважением, Фролов Никита Дежурный инженер СТПиЭ A1 Systems Моб.: +7 (903)-210-81-98 E-mail: n.frolov@a1-systems.com Информация, содержащаяся в данном сообщении, является КОММЕРЧЕСКОЙ ТАЙНОЙ, и предназначена для строго определенного круга лиц. Если данное сообщение попало к Вам по ошибке, немедленно удалите его. Незаконное использование, копирование, распространение вышеуказанной информации влечет уголовную, административную, гражданско-правовую...   
5179       C уважением, Фролов Никита Дежурный инженер СТПиЭ A1 Systems Моб.: +7 (903)-210-81-98 E-mail: n.frolov@a1-systems.com Информация, содержащаяся в данном сообщении, является КОММЕРЧЕСКОЙ ТАЙНОЙ, и предназначена для строго определенного круга лиц. Если данное сообщение попал

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [15]:
for cls in df['topic'].unique():
    print(f"Предварительное количество объектов с темой {cls}: {df[df['topic'] == cls].shape[0]}")

Предварительное количество объектов с темой 9: 438
Предварительное количество объектов с темой 5: 4825
Предварительное количество объектов с темой 1: 891
Предварительное количество объектов с темой 2: 1135
Предварительное количество объектов с темой 3: 772
Предварительное количество объектов с темой 6: 440
Предварительное количество объектов с темой 0: 535
Предварительное количество объектов с темой 4: 509
Предварительное количество объектов с темой 8: 320
Предварительное количество объектов с темой 7: 407


## Темы "Технические оповещения" (тесты, предупреждения) и "Спам"

In [ ]:
display(df[df['topic'] == 4]['theme'].value_counts())

theme
Уведомление от Мегаком                                                       20
Обращения абонента "Семья здесь"                                             11
Семья здесь                                                                   9
RE: A1S: Политика обновления вашего пароля                                    8
Бизнес-поиск                                                                  6
                                                                             ..
IM00078869                                                                    1
белоруснефть_бизнес поиск                                                     1
IM00077974                                                                    1
семья здесь IM00078716                                                        1
Продолжается льготная регистрация на XI международный форум ProfComm 2024     1
Name: count, Length: 423, dtype: int64

In [16]:
df.query('theme == "Уведомление от Мегаком"')['topic'].value_counts()

topic
4    20
Name: count, dtype: int64

In [17]:
assign_cluster(df, 'theme', 'Уведомление от Мегаком')

theme  topic  \
3953  Уведомление от Мегаком      4   
4318  Уведомление от Мегаком      4   
4459  Уведомление от Мегаком      4   
4512  Уведомление от Мегаком      4   
4593  Уведомление от Мегаком      4   
4594  Уведомление от Мегаком      4   
4876  Уведомление от Мегаком      4   
5136  Уведомление от Мегаком      4   
5510  Уведомление от Мегаком      4   
5852  Уведомление от Мегаком      4   
6551  Уведомление от Мегаком      4   
6552  Уведомление от Мегаком      4   
6948  Уведомление от Мегаком      4   
7850  Уведомление от Мегаком      4   
7979  Уведомление от Мегаком      4   
8297  Уведомление от Мегаком      4   
8709  Уведомление от Мегаком      4   
9357  Уведомление от Мегаком      4   
9358  Уведомление от Мегаком      4   
9481  Уведомление от Мегаком      4   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        descr  \
3953  Здравствуйте! Согласно п.3 Приложения № 3 к заключенному Договору денежные средства в размере 167.20 сом будут удержаны из вознаграждения, причитающегося Провайдеру за оказанные услуги за текущий месяц 2023 года. № Жалобы:1297211 Сумма:167.20 Номер:996555455111 Во избежание повторения подобной ситуации, убедительно просим Вас обеспечить надлежащую работу услуги. Данное оповещение сформировано автоматически, в случае возникновения дополнительных вопросов Вы можете обратится к спец...   
4318  Здравствуйте! Согласно п.3 Приложения № 3 к заключенному Договору денежные средства в размере 250.80 сом будут удержаны из вознаграждения, причитающегося Провайдеру за оказанные услуги за текущий месяц 2023 года. № Жалобы:1300922 Сумма:250.80 Номер:996550802431 Во избежание повторения подобной ситуации, убедительно просим Вас обеспечить надлежащую работу услуги. Данное оповещение сформировано автоматически, в случае возникновения дополнительных вопросов Вы можете обратится к спец...   
4459  Здравствуйте! Согласно п.3 Приложения № 3 к заключенному Договору денежные средства в размере 188.10 сом будут удержаны из вознаграждения, причитающегося Провайдеру за оказанные услуги за текущий месяц 2023 года. № Жалобы:1302257 Сумма:188.10 Номер:996555745063 Во избежание повторения подобной ситуации, убедительно просим Вас обеспечить надлежащую работу услуги. Данное оповещение сформировано автоматически, в случае возникновения дополнительных вопросов Вы можете обратится к спец...   
4512  Здравствуйте! Согласно п.3 Приложения № 3 к заключенному Договору денежные средства в размере 209 сом будут удержаны из вознаграждения, причитающегося Провайдеру за оказанные услуги за текущий месяц 2023 года. № Жалобы:1302594 Сумма:209 Номер:996550398314 Во избежание повторения подобной ситуации, убедительно просим Вас обеспечить надлежащую работу услуги. Данное оповещение сформировано автоматически, в случае возникновения дополнительных вопросов Вы можете обратится к специалист...   
4593  Здравствуйте! Согласно п.3 Приложения № 3 к заключенному Договору денежные средства в размере 41.8 сом будут удержаны из вознаграждения, причитающегося Провайдеру за оказанные услуги за текущий месяц 2023 года. № Жалобы:1303156 Сумма:41.8 Номер:996999554491 Во избежание повторения подобной ситуации, убедительно просим Вас обеспечить надлежащую работу услуги. Данное оповещение сформировано автоматически, в случае возникновения дополнительных вопросов Вы можете обратится к специали...   
4594  Здравствуйте! Согласно п.3 Приложения № 3 к заключенному Договору денежные средства в размере 83.6 сом будут удержаны из вознаграждения, причитающегося Провайдеру за оказанные услуги за текущий месяц 2023 года. № Жа

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [18]:
assign_cluster(df, 'theme', 'Mass Mail', exact_match=False, exclude_keywords=['Жалоба', 'запрос кп'])
# явно наспамили

theme  \
214                                                          [!!Mass Mail]Семинар - Командировочные и представительские расходы. Новые требования к документированию.   
501                                                                         [!!Mass Mail]Предложение о привлечении клиентов из digital каналов от Gramor Studio (СРА)   
643                                                           [!!Mass Mail]Отбор заявок на участие в программе «выращивания» Группы «Интер РАО» с 1 февраля 2023 года   
725                                                     [!!Mass Mail]Сочи! Бухгалтерский и налоговый учет в 2023 году: Актуальные вопросы. Обзор последних изменений.   
912                                                                          [!!Mass Mail]Сочи / Семинар -практикум / Оптимизация налогов в эпоху цифрового контроля.   
966                                                                                          [!!Mass Mail]Идеальные КУЛИЧИ - коломбы и торты уже прибыли! Пасха 2023!   
1000                                                                                                     [!!Mass Mail]Оптимизация налогов в эпоху цифрового контроля.   
1043                                                                                                                            [!!Mass Mail]Новый лизинговый партнер   
1099                                                                                                                               [!!Mass Mail]Digital трансформация   
1121                                                                                                        [!!Mass Mail]?? Романтический ужин с Продуктами из Италии   
1125                                                                                  [!!Mass Mail]Семинар по оптимизации налогов. Красная поляна / Отель Green Flow.   
1145                                                                  [!!Mass Mail]Изменения порядка уплаты НДС налоговым агентом и формы налоговой декларации по НДС   
1167                                                                                  [!!Mass Mail]Семинар по оптимизации налогов. Красная поляна / Отель Green Flow.   
1214                                                                                  [!!Mass Mail]Семинар по оптимизации налогов. Красная поляна / Отель Green Flow.   
1305                                                                                               [!!Mass Mail]?? Международный Мужской День с Продуктами из Италии!   
1333                                                                                  [!!Mass Mail]Онлайн-конференция: Новое в бухгалтерском учете и налогообложении.   
1551                                                                                     [!!Mass Mail]-20% на все букеты! Розы и Тюльпаны к 8 марта с доставкой 24/7!   
1660                                    [!!Mass Mail]Конференция (очно и онлайн): Бухгалтер 2023: экспертный анализ последних изменений. Новое в бухгалтерском учете.   
1813                                                                                                [!!Mass Mail]Налоговая оптимизация в условиях цифрового контроля.   
1921                                    [!!Mass Mail]ВЕБИНАР: «МОРАТОРИЙ: В 2023 ГОДУ ФНС ТРЕБУЕТ УПЛАТИТЬ КАК ВЗНОС 30% ПРИБЫЛИ/ДИВИДЕНДОВ, РАСПРЕДЕЛЕННЫХ В 2022 Г»   
2079                                                                                               [!!Mass Mail]Are you targeting East Europe and Middle East market?   
2081                                                                                                   [!!Mass Mail]??Сочи 2-3 мая. Семинар по налоговой оптимизации.   
2193                                                                                                                  [!!Mass Mail]Грант на приобретение оборудование   
2247                                                                                                    

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

![Alt Text](https://memi.klev.club/uploads/posts/2024-04/memi-klev-club-5g6z-p-memi-kot-v-vode-11.jpg)



In [23]:
df['cluster'].value_counts()

cluster
9    161
8     89
Name: count, dtype: int64

In [ ]:
display(df[df['topic'] ==8]['theme'].value_counts())

theme
дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)    51
Рассылки и PUSH уведомление                                                 46
рассылки и PUSH уведомление                                                 38
Undeliverable: Kcell Лотерея                                                15
[!!Mass Mail]This Week's Edition of the Canarsie Courier                    13
                                                                            ..
Рассылки и PUSH Уведомление                                                  1
Уведомления                                                                  1
Рассылки и PUSH уведомлениме                                                 1
Push увежомление и рассылки                                                  1
[!!Mass Mail]Selectel приглашает на бизнес-завтрак                           1
Name: count, Length: 110, dtype: int64

In [20]:
assign_cluster(df, 'theme', 'дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)')

theme  \
445   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
505   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
509   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
610   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
646   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
734   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
792   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
831   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
917   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
951   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
954   дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1036  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1131  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1132  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1194  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1288  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1289  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1636  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1894  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
1895  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2106  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2115  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2244  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2308  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2354  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2363  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2377  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2425  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2700  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2875  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2894  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
2929  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3014  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3017  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3052  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3112  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3169  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3198  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3453  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3505  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3549  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3665  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3721  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
3788  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
4063  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
4199  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
4331  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
4357  дд прошу удалить пуш уведомление дов платеж и дов гб за ранее спасибо :)   
4605  дд прошу удалить пуш уведомление дов платеж и дов

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [35]:
assign_cluster(df, 'theme', 'PUSH', exact_match=False, exclude_keywords=['отказ', 'мегафон', 'билайн'])

theme  topic  \
135                  RE: PUSH Tele2Pay      3   
1422                  push уведомления      8   
3040                              Push      8   
3173        Рассылки /PUSH уведомление      8   
3174       рассылки и PUSH уведомление      8   
3176        рассылки- PUSH уведомление      8   
3179       рассылки и PUSH уведомление      8   
3199       рассылки и PUSH уведомление      8   
3201       рассылки и PUSH уведомление      8   
3202       рассылки и PUSH уведомление      8   
3203       рассылки и PUSH уведомление      8   
3204       рассылки и PUSH уведомление      8   
3211       рассылки и PUSH уведомление      8   
3216       рассылки и PUSH уведомление      8   
3219       рассылки и PUSH уведомление      8   
3220       рассылки и PUSH уведомление      8   
3222       рассылки и PUSH уведомление      8   
3223       рассылки и PUSH уведомление      8   
3232       Рассылки и PUSH уведомление      8   
3248       рассылки и PUSH уведомление      8   
3249       рассылки и PUSH уведомление      8   
3281       рассылки и PUSH уведомление      8   
3289       рассылки и Push уведомление      8   
3290       рассылки и PUSH уведомление      8   
3315       рассылки и PUSH уведомление      8   
3319       Рассылки и PUSH уведомление      8   
3320       рассылки и PUSH уведомление      8   
3321       рассылки и PUSH уведомление      8   
3330       рассылки и PUSH уведомление      8   
3331       рассылки и PUSH уведомление      8   
3332       рассылки и PUSH уведомление      8   
3333       рассылки и PUSH уведомление      8   
3354        расылки и PUSH уведомление      8   
3357       рассылки и PUSH уведомление      8   
3384       Рассылки и PUSH уведомление      8   
3389       Рассылки и PUSH уведомление      8   
3437       рассылки и PUSH уведомление      8   
3438       рассылки и PUSH уведомление      8   
3443       рассылки и PUSH уведомление      8   
3445       рассылки и PUSH уведомление      8   
3454       рассылки и PUSH уведомление      8   
3492       Рассылки и PUSH уведомление      8   
3498       Рассылки и PUSH уведомление      8   
3548       рассылки и PUSH уведомление      8   
3573       Рассылки и PUSH уведомление      8   
3576       Рассылки и PUSH уведомление      8   
3600       Рассылки и PUSH уведомление      8   
3606       рассылки и PUSH уведомление      8   
3678       рассылки и PUSH уведомление      8   
3700       Рассылки и PUSH уведомление      8   
3704       Рассылки и PUSH уведомление      8   
3712       рассылки и PUSH уведомление      8   
3713       рассылки и PUSH уведомление      8   
3714       Рассылки и PUSH уведомление      8   
3741       рассылки и PUSH уведомление      8   
3823       Рассылки и PUSH уведомление      8   
3844       Рассылки и PUSH уведомление      8   
3882       Рассылки и PUSH уведомление      8   
3896       Рассылки и PUSH уведомление      8   
3914       рассылки и PUSH уведомление      8   
3935       рассылки и PUSH уведомление      8   
4035       Рассылки и PUSH уведомление      8   
4036       Рассылки и Push уведомление      8   
4154       Рассылки и PUSH уведомление      8   
4191       Push увежомление и рассылки      8   
4207       Рассылки и PUSH уведомление      8   
4222      Рассылки и PUSH уведомлениме      8   
4229       Рассылки и PUSH уведомление      8   
4311       Рассылки и Push уведомление      8   
4315       Рассылки и PUSH уведомление      8   
4352       Рассылки и PUSH уведомление      8   
4353       Рассылки и PUSH уведомление      8   
4392       Рассылки и PUSH уведомление      8   
4434       Рассылки и PUSH уведомление      8   
4458       Рассылки и PUSH уведомление      8   
4479       Рассылки и PUSH уведомление      8   
4570       Рассылки и PUSH уведомление      8   
4574       Рассылки и PUSH Уведомление      8   
4600       Рассылки и PUSH уведомление      8   
4672       Рассылки и PUSH уведомление      8   
4675       Рассылки и PUSH уведомление      8   
4676       Расс

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [37]:
assign_cluster(df, 'theme', 'PUSH', exact_match=False, exclude_keywords=['мегафон', 'билайн'])

theme  topic  \
60                 Отказ от push-уведомлений      6   
85                 Отказ от push-уведомлений      6   
107                Отказ от push-уведомлений      6   
245                Отказ от push-уведомлений      6   
287                Отказ от push-уведомлений      6   
359                Отказ от push-уведомлений      6   
433                Отказ от push-уведомлений      6   
439                Отказ от push-уведомлений      6   
612                Отказ от push-уведомлений      6   
613                Отказ от push-уведомлений      6   
662                Отказ от push-уведомлений      6   
681                Отказ от push-уведомлений      6   
730                Отказ от push-уведомлений      6   
813                Отказ от push-уведомлений      6   
816                Отказ от push-уведомлений      6   
869                Отказ от push-уведомлений      6   
985                Отказ от push-уведомлений      6   
1070               Отказ от push-уведомлений      6   
2908               Отказ от push-уведомлений      6   
3076               Отказ от push-уведомлений      6   
3345              Отказ от push-уведомлений»      6   
3419               Отказ от push-уведомлений      6   
3649    Отказ от push-уведомлений 2267544972      6   
3650    Отказ от push-уведомлений 2267544501      6   
3653    Отказ от push-уведомлений 2267560759      6   
3675    Отказ от push-уведомлений 2267769945      6   
3701    Отказ от push-уведомлений 2267842885      6   
3723             «Отказ от push-уведомлений»      6   
3740    Отказ от push-уведомлений 9636247438      6   
3770    Отказ от push-уведомлений 9094877770      6   
3818    Отказ от push-уведомлений 9640183973      6   
3946    Отказ от push-уведомлений 9618178819      6   
4126    Отказ от push-уведомлений 9610758271      6   
4127    Отказ от push-уведомлений 9606871199      6   
4158    Отказ от push-уведомлений 9037229942      6   
4257    Отказ от push-уведомлений 9057568777      6   
4368               Отказ от push-уведомлений      6   
4371               Отказ от push-уведомлений      6   
4575    Отказ от push-уведомлений 9039338208      6   
4576    Отказ от push-уведомлений 9260030020      6   
4578    Отказ от push-уведомлений 9610524341      6   
4580    Отказ от push-уведомлений 9654450162      6   
4581    Отказ от push-уведомлений 9613177703      6   
4582    Отказ от push-уведомлений 9667152307      6   
4583    Отказ от push-уведомлений 9037238929      6   
4596    Отказ от push-уведомлений 9654754434      6   
4599    Отказ от push-уведомлений 9654666185      6   
4619               Отказ от push-уведомлений      6   
4629    Отказ от push-уведомлений 9656254967      6   
4630    Отказ от push-уведомлений 9036264346      6   
4641    Отказ от push-уведомлений 9033370549      6   
4642    Отказ от push-уведомлений 9603724449      6   
4643    Отказ от push-уведомлений 9603665052      6   
4644    Отказ от push-уведомлений 9677741047      6   
4652    Отказ от push-уведомлений 9674086135      6   
4724    Отказ от push-уведомлений 9067259662      6   
4740    Отказ от push-уведомлений 9056691175      6   
4753    Отказ от push-уведомлений 9628511033      6   
4774    Отказ от push-уведомлений 9608617158      6   
4821    Отказ от push-уведомлений 9673651904      6   
4853    Отказ от push-уведомлений 9624051822      6   
4867    Отказ от push-уведомлений 9679424522      6   
4868    Отказ от push-уведомлений 9032747560      6   
4869    Отказ от push-уведомлений 9696245740      6   
4870    Отказ от push-уведомлений 9632646012      6   
4878    Отказ от push-уведомлений 9620120248      6   
4902    Отказ от push-уведомлений 9681511226      6   
4906    Отказ от push-уведомлений 9250205793      6   
4907    Отказ от push-уведомлений 9051987929      6   
4931    Отказ от push-уведомлений 9697659545      6   
4961    Отказ от push-уведомлений 9619433775      6   
4963    Отказ от push-уведомлений 9633727228      6   
5020    Отказ от push-ув

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [42]:
assign_cluster(df, 'theme', 'запись', exact_match=False)

theme  \
132                                                        Mobile ID. Учетная запись Мерател ООО (Мегафон)   
312                                                        RE: Учетная запись Интернет-банк "Долинск"(МТС)   
386                                                 Mobile ID. Учетная запись Интернет-банк "Долинск"(МТС)   
387                                                   Mobile ID. Учетная запись Пятый Элемент Деньги (МТС)   
388                                            Mobile ID. Учетная запись Автокомплекс «ЕвроАвто» (Мегафон)   
502                                                                       Mobile ID. Учетная запись Gipfel   
549                                            Mobile ID. Учетная запись Банк Оранжевый (Билайн) изменения   
794                                                     Mobile ID. Изменения в Учетную запись Бельетаж ООО   
942                                                        Mobile ID. Учетная запись  vipfish.ru (Мегафон)   
1004                                                 Mobile ID. Учетная запись  solid-mn.ru аутентификация   
1094                                                           Mobile ID. Учетная запись superapteka (МТС)   
1098                              FW: Учетная запись Нетмонет (Билайн) перевод в коммерческую эксплуатацию   
1158                                                           Mobile ID. Учетная запись BookHead (Билайн)   
1159                                                           Mobile ID. Учетная запись Источник (Билайн)   
1311                                               Mobile ID. Изменение в учетную запись istochnik_beeline   
1423                                                               Mobile ID. Учетная запись Unibell (МТС)   
1424                                                         Mobile ID. Учетная запись  Банки.ру (мегафон)   
1515                                            Mobile ID. Учетная запись: Терминал_Нефть_Эксперт (Билайн)   
1516                                                          Mobile ID. Учетная запись  Quick Resto (МТС)   
1539                                                Mobile ID. Учетная запись ivi (МТС) внесение изменений   
1602                                           Mobile ID. Учетная запись Benefit Vantage Limited отключить   
1752                                                       Mobile ID. Учетная запись Bankiros.ru (Мегафон)   
1753                                                      Mobile ID. Учетная запись client_id=BELETAZH_LLC   
1816                                                               Mobile ID. Учетная запись unibell (МТС)   
1817                                               Mobile ID. Учетная запись Оператор Газпром ИД (Мегафон)   
2069                                                      Mobile ID. Учетная запись  solid-mn.ru изменение   
2070                                                              Мобильный ИД учетная запись Avenda (МТС)   
2178                                                           Mobile ID. Учетная запись mobile.wifi (RTK)   
2230                                                   Mobile ID. Учетная запись Фарм консалтинг (Мегафон)   
2231                                  Mobile ID. Учетная запись ИП Хамицкий Александр Николаевич (Мегафон)   
2336                                                             Mobile ID. Учетная запись Нияма (Мегафон)   
2337                                                           Mobile ID. Учетная запись Sarawan (Мегафон)   
2338                                                          Mobile ID. Учетная запись Цветторг (Мегафон)   
2339                                                          FMobile ID. Учетная запись zonatelecom (МТС)   
2406                                                        Mobile ID. Учетная запись klubok.club (Билайн)   
2485                                                             Mobile ID. Учетная запись  Areal (Билайн)   
2566                           

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [47]:
assign_cluster(df, 'descr', ['учетная', 'запись'], exact_match=False)

theme  \
128                                 MobileID. изменить УЗ билайн ЛК B2B   
133                                 MobileID. изменить УЗ билайн ЛК B2B   
436                                       FW: MobileID. УЗ Аптека легко   
1603                                     MobileID. Изменить УЗ Источник   
1608                                   MobileID. УЗ Unibell (Вымпелком)   
1665                              FW: Настройки УЗ Terminal_Neft_Expert   
1783                                    FW: УЗ Getski.me для unibell.ru   
1818                           MobileID. УЗ Unibell Вымпелком) удаление   
2004                                      FW: Создание УЗ Мой дом (МТС)   
2066                                  FW: MobileID. Телефон_IP (Билайн)   
2067                           FW: MobileID. УЗ Облачные кассы (Билайн)   
2068                                        FW: MobileID. Скад (Билайн)   
2650                                    FW: MobileID. Heineken (Билайн)   
2669                    MobileID изменение УЗ Фарм_консалтинг_(Мегафон)   
2756                                     Мобильный ИД, УЗ svm24 (Tele2)   
3164                                                FW: УЗ АСК-ИТ (МТС)   
3542                           FW: Мобильный ИД, УЗ stroyudacha (Tele2)   
4067                              Mobile ID. Client_name: Миговеб (МТС)   
4068                   Mobile ID. Client_name: wildberries.ru (Мегафон)   
4069            Mobile ID.  Client_name: MegaFon WiFi (Tele2) изменения   
4132                      Mobile ID. Client_name: asklepiy-dv (мегафон)   
4136                             Mobile ID. Client_name: Старт.Ру (МТС)   
4137                             Mobile ID. Client_name: Буратино (МТС)   
4187                               Mobile ID. Client_name: WIFI Beeline   
4190                    MobileID изменение УЗ Фарм_консалтинг_(Мегафон)   
4244    Mobile ID. Client_name: politek-service.ru (Мегафон) измененить   
4277                                     FW: MobileID. Centra.Дом Теле2   
4279                                Mobile ID Client_name: Займиго(МТС)   
4282           Mobile ID. Client_name: МЕДИЦИНСКАЯ КЛИНИКА АВРОРА (МТС)   
4283                               Mobile ID. Client_name: Аконит (МТС)   
4967                Mobile ID.  Client_name: Intersvyaz (МТС) изменение   
4968           RE: Mobile ID.  Client_name: 33komoda.ru (МТС) изменение   
4969               Mobile ID.  Client_name: 33komoda.ru (МТС) изменение   
4972                     Mobile ID.  Client_name: megatel_mts изменение   
4973                              Mobile ID. Client_name: билайн облако   
5035                             РУП кадастровое агентство_бизнес поиск   
5209                                   MobileID. УЗ rumbra.ru (Мегафон)   
5210                            MobileID. УЗ для kruiz.online (Мегафон)   
5212                                      FW: MobileID. УЗ Ареал билайн   
5213                                      MobileID. УЗ Рататуй (Билайн)   
5214                    MobileID. УЗ  Внедренческий Центр - Вятка (МТС)   
5215                                         MobileID. УЗ Basis(Билайн)   
5216                                         MobileID. УЗ  SCAD(Билайн)   
5323                                      MobileID УЗ Oboideco (Билайн)   
5324                                  MobileID. УЗ terasms.ru (Мегафон)   
5325                                   MobileID. УЗ  ShopPoker (Билайн)   
5326                                   MobileID УЗ bxmaker.ru (Мегафон)   
5327                             MobileID УЗ quick-finance.ru (Мегафон)   
5328                                  MobileID УЗ ЧИСТОСТРАНА (Мегафон)   
5329                              MobileID. УЗ music(beeline) изменение   
5330                                  MobileID УЗ lk.tgc-2.ru (Мегафон)   
5331                                                    FW: УЗ NetbyNet   
5332                   MobileID УЗ Международный Юридический Клуб (МТС)   
5416            

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [53]:
assign_cluster(df, 'theme', 'ЧС ', exact_match=False)

theme  topic  \
6                      ЧС по 99993 от 01.01.2023      5   
12                     ЧС по 99993 от 02.01.2023      5   
18                     ЧС по 99993 от 03.01.2023      5   
48                     ЧС по 99993 от 04.01.2023      5   
62                     ЧС по 99993 от 05.01.2023      5   
79                     ЧС по 99993 от 06.01.2023      5   
95                     ЧС по 99993 от 07.01.2023      5   
109                    ЧС по 99993 от 08.01.2023      5   
126                                ЧС 09.01.2023      0   
139                    ЧС по 99993 от 09.01.2023      5   
174                    ЧС по 99993 от 10.01.2023      5   
188             срочно добавить в ЧС 79647809230      0   
194                    ЧС по 99993 от 11.01.2023      5   
220                    ЧС по 99993 от 12.01.2023      5   
246             срочно добавить в ЧС 79039789933      0   
257                    ЧС по 99993 от 13.01.2023      5   
276                    ЧС по 99993 от 14.01.2023      5   
290                    ЧС по 99993 от 15.01.2023      5   
321    Извлечь из ЧС по 99993 номер 375259183472      0   
324                    ЧС по 99993 от 16.01.2023      5   
363                    ЧС по 99993 от 17.01.2023      5   
390                                ЧС 18.01.2023      0   
395                    ЧС по 99993 от 18.01.2023      5   
414                    ЧС по 99993 от 19.01.2023      5   
448                    ЧС по 99993 от 20.01.2023      5   
459                    ЧС по 99993 от 21.01.2023      5   
482                    ЧС по 99993 от 22.01.2023      5   
507                    ЧС по 99993 от 23.01.2023      5   
555                    ЧС по 99993 от 24.01.2023      5   
589                    ЧС по 99993 от 25.01.2023      5   
600          ЧС по 99993 от 26.01.2023 (часть 1)      5   
611                    ЧС по 99993 от 26.01.2023      5   
635                ЧС по 99993 от 26.01.2023 (1)      5   
640    Извлечь из ЧС по 99993 номер 375257856867      0   
656                    ЧС по 99993 от 27.01.2023      5   
664          ЧС по 99993 от 27.01.2023 (2 часть)      5   
667    Извлечь из ЧС по 99993 номер 375256515079      0   
682                    ЧС по 99993 от 28.01.2023      5   
721                    ЧС по 99993 от 29.01.2023      5   
762                           ЧС по 99993 январь      5   
763                    ЧС по 99993 от 30.01.2023      5   
784                    ЧС по 99993 от 31.01.2023      5   
819                                ЧС 02.02.2023      0   
827                    ЧС по 99993 от 01.02.2023      5   
835                    ЧС по 99993 от 02.02.2023      5   
863                    ЧС по 99993 от 03.02.2023      5   
874                    ЧС по 99993 от 04.02.2023      5   
906                    ЧС по 99993 от 05.02.2023      5   
943                    ЧС по 99993 от 06.02.2023      5   
971                    ЧС по 99993 от 07.02.2023      5   
999                    ЧС по 99993 от 08.02.2023      5   
1030                   ЧС по 99993 от 09.02.2023      5   
1066                   ЧС по 99993 от 10.02.2023      5   
1073                   ЧС по 99993 от 11.02.2023      5   
1097                   ЧС по 99993 от 12.02.2023      5   
1129                   ЧС по 99993 от 13.02.2023      5   
1155                   ЧС по 99993 от 14.02.2023      5   
1193                   ЧС по 99993 от 15.02.2023      5   
1195                               ЧС 16.02.2023      0   
1204   Извлечь из ЧС по 99993 номер 375257873204      0   
1215                   ЧС по 99993 от 16.02.2023      5   
1242                   ЧС по 99993 от 17.02.2023      5   
1262                   ЧС по 99993 от 18.02.2023      5   
1282                   ЧС по 99993 от 19.02.2023      5   
1314                   ЧС по 99993 от 20.02.2023      5   
1334                   ЧС по 99993 от 21.02.2023      5   
1364                   ЧС по 99993 от 22.02.2023      5   
1380                   ЧС по 99

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [58]:
assign_cluster(df, 'theme', ['отключение', 'услуг'], exact_match=False, exclude_keywords=['поставщик', 'Sim-reminder', 'даты Лота', 'SMSC', 'исследовании' ])

theme  topic  \
10                                                     отключение      9   
52                                                     Отключение      8   
412                 Отключение от рассылки "Доверительный платеж"      8   
2026                                            Отключение услуги      0   
2252                               375255245422, отключение 99993      5   
2503                              375256511579 - отключение 99993      5   
2825                                             отключение услуг      6   
3021                                            отключение услугу      8   
3615   Удалить услугу Технологическая: Администратор Бизнес Поиск      4   
3752                отключение от рассылки "доверительный платеж"      8   
3976                отключение от рассылки "доверительный платеж"      8   
4055                             Отключение подписок на М-портале      0   
4157                             Бизнес-поиск: не работает услуга      4   
4194               Отключение от рассылки «Доверительный платеж».      6   
4517                                     Отключение контент услуг      0   
4743          Жалоба абонента на услугу "Живой баланс" TT23248326      2   
4767      Запрос на отключение алгоритмов на интерфейсе https ota      3   
5092                                        Re: отключение услуги      0   
5597                                      Отключение от рассылок.      8   
5701                отключение от рассылки "доверительный платеж"      8   
6296                отключение от рассылки "доверительный платеж"      8   
6905                                            Отключение LBS_A1      4   
7003                                        Отключение доп.услуги      6   
7215                                            Отключение LBS_A1      4   
7258   Приглашение на участие в конкурентных закупках работ/услуг      6   
7434                       Удаляется услуга Семья здесь error 500      4   
7512                                                   Отключение      0   
7712                           LBS: Удаление услуги "Семья здесь"      4   
7763                  FW: Аквафон. Запрос факта подключения услуг      7   
7829                           отключение номера от контент услуг      9   
7830                                     отписка от контент услуг      9   
7866                RE: Не работает сайт отключения контент услуг      4   
8296                      Обращение абонента услуги "Семья здесь"      4   
8350                                     отключение от доп услуги      9   
8524                                             Отключение услуг      0   
8822                           Замена URL для услуги IMEI Tracker      4   
9079                                           Тестирование услуг      4   
9871                                   отключение услуги smarbook      9   
10103                                              Отключение B2B      6   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            descr  \
10                                                                                                                                                                                                                                                                                                                                                                Добрый день! Прошу отключить абоненту 992929146979 все услуги. По его словам не отключается – уточните плз причину. BR Shavkat    
52                                               

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [63]:
assign_cluster(df, 'descr', ['отключить на номере абонента сервис'], exact_match=False)

theme  topic  \
423    Жалоба абонента TT20744657      9   
432       Живой баланс TT20750294      9   
518       Живой баланс TT20778143      9   
602             Жалоба TT20796241      9   
934       Живой баланс TT20894816      9   
1331            Жалоба TT21027501      9   
1530            Жалоба TT21103392      9   
1731            Жалоба TT21192531      9   
1741            Жалоба TT21195510      9   
1809            Жалоба TT21231393      9   
1815            Жалоба TT21223792      9   
1861      Живой баланс TT21260484      9   
2007            Жалоба TT21315175      2   
2048            Жалоба TT21346367      2   
2168      Живой баланс TT21401865      9   
3496      Живой баланс TT22205663      9   
3596            Жалоба TT22267209      9   
3610            Жалоба TT22277315      9   
4288      Живой баланс TT22873346      9   
4306      Живой баланс TT22890474      9   
4411      Живой баланс TT22983077      9   
5614            Жалоба TT24001072      9   
5644      Живой баланс TT24012773      9   
5645      Живой баланс TT24034237      9   
5734      Живой баланс TT24097626      9   
7402  Жалоба абонента  TT25907720      9   
7444            Жалоба TT25914797      9   
9198            Жалоба TT28111089      9   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 descr  \
423                              Добрый день! Коллеги, прошу отключить на номере абонента сервис «Tele2-Тема» и внести его в чёрный список. 0. Номер абонента : 79006645008 1. Дата и время заказа : 21 декабря 2. Номер провайдера (для КЦ из InVoice / для розницы - номер подписки из WD) : -- 3. Описание проблемы : абоненту поступают SMS, хотя он отключал 4. Текст сообщения на экране телефона (не путать с Tele2 тема) : скрин приложила Просим ответить в течение 24 час...   
432                            Доброго времени суток! Коллеги, прошу отключить на номере абонента сервис «Живой баланс» и внести его в чёрный список. Прошу отправить команду на отключение SIM-reminder. Номер абонента: 79155573876 Просим ответить в течение 24 часов на адрес content_problem@tele2.ru. Спасибо за сотрудничество. С наилучшими пожеланиями, Шилов Павел. Специалист по обработке клиентских запросов Сервисный центр клиентских бэк-офисных операций Контактны...   
518             Доброго времени суток! Коллеги, прошу отключить на номере абонента сервис «Живой баланс» и внести его в чёрный список. Прошу отправить команду на отключение SIM-reminder. Номер абонента: 79155573876, абонент обращается повторно Просим ответить в течение 24 часов на адрес content_problem@tele2.ru. Спасибо за сотрудничество. С наилучшими пожеланиями, Шилов Павел. Специалист по обработке клиентских запросов Сервисный центр клиентских бэк-офисных опер...   
602                                                                                                                                    Добрый день! Коллеги, прошу отключить на номере абонента сервис «Tele2-Тема» и внести его в чёрный список. Просим ответить в течение 24 часов на адрес content_problem@tele2.ru. Спасибо за сотрудничество. С наилучшими пожеланиями, Специалист по обработке клиентских запросов Сервисный центр клиентских бэк-офисных операций Tele2 Россия    
934                            Доброго времени суток! Коллеги, прошу отключить на номере абонента сервис «Живой баланс» и внести его в чёрный список. Прошу отправить команду на отключение SIM-reminder. Номер абонента: 79991580889 Просим ответить в течение 24 часов на адрес content_problem@tele2.ru. Спасибо за сотрудничество. С наилучшими пожеланиями, Шилов Павел. Специалист по о

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [64]:
assign_cluster(df, 'descr', ['сим-меню'], exact_match=False)

theme  \
7562                                         Жалоба абонента  TT25998467   
9553  Работа е-сим за границей_Левшенкова Екатерина Борисовна_9844605651   

      topic  \
7562      9   
9553      4   

                                                                                                                                                                                                                                                                                                                                                                                                                                                descr  \
7562     Доброго времени суток! Просьба отключить сим меню 0. Номер абонента : 79043339088 1. Дата и время заказа : 20.03.2024 15:39 2. Номер провайдера (для КЦ из InVoice / для розницы - номер подписки из WD) : отключить сим-меню 3. Описание проблемы : не может отключить 4. Текст сообщения на экране телефона (не путать с Tele2 тема) : service not available ПРОСЬБА ПРИ ОТВЕТЕ НА ЗАПРОС ИСПОЛЬЗЬЗОВАТЬ ФУНКЦИЮ "ОТВЕТИТЬ ВСЕМ&amp;quo...   
9553   Добрый день! Левшенкова Екатерина Борисовна 9844605651 89701452270000162031 У клиента е-сим, проживает в Италии, нет сети. Сим-меню не доступно. Прошу проверить информацию по работе е-сим. Описание проблемы: Сегодня, 3 августа 2024 года в районе 19.05-19.10 очередная попытка дождаться "ответа" от e-sim. Ситуация не меняется. В разделе "Мобильная связь - управление sim-картами" активирована e-sim. Она отображается как включе...   

                        sender_name  
7562                content_problem  
9553  Яковлева Анастасия Викторовна

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [65]:
assign_cluster(df, 'descr', ['сим меню'], exact_match=False)

theme  topic  \
421          Жалоба абонента  TT20741751      9   
627           Жалоба абонента TT20806339      9   
991          Жалоба абонента  TT20909365      9   
1211         Жалоба абонента  TT20981665      9   
1613         Жалоба абонента  TT21134033      9   
1720         Жалоба абонента  TT21187667      9   
1721         Жалоба абонента  TT21187667      9   
1808         Жалоба абонента  TT21229399      9   
2062         Жалоба абонента  TT21350135      9   
2138         Жалоба абонента  TT21385965      9   
2528                   Жалоба TT21638835      9   
3905                   Жалоба TT22519895      9   
3969          Жалоба абонента. 917000657      9   
4071          Жалоба абонента TT22656639      9   
4471                   Жалоба TT23031423      9   
5177         Жалоба абонента  TT23631868      9   
5478                   Жалоба TT23893847      9   
5672                   Жалоба TT24053683      9   
6222                 Сим меню 2915275101      9   
7196         Жалоба абонента  TT25649424      9   
7314         Жалоба абонента  TT25837494      9   
7698         Жалоба абонента  TT26147999      9   
7796          Жалоба абонента TT26266128      9   
7813         Жалоба абонента  TT26277360      9   
7965           жалоба абонент TT26431511      9   
8265          Жалоба абонента TT26807253      9   
8300  Жалоба абонента. Заявка TT26848478      9   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 descr  \
421                                            Доброго времени суток! 0. Номер абонента : 79255520111 1. Дата и время заказа : 19.01.23 9:10 2. Номер провайдера (для КЦ из InVoice / для розницы - номер подписки из WD) : сим меню 3. Описание проблемы : пишет что откл, но не пропадает 4. Текст сообщения на экране телефона (не путать с Tele2 тема) : - ПРОСЬБА ПРИ ОТВЕТЕ НА ЗАПРОС ИСПОЛЬЗЬЗОВАТЬ ФУНКЦИЮ "ОТВЕТИТЬ ВСЕМ" Просим ответить в течение 24 часов на адрес content_problem@tele...   
627                          Добрый день, коллеги! Просьба проверить жалобу абонента. 0. Номер абонента : 79921311017 1. Дата и время заказа : 26.01.23 00:55 местное 2. Номер провайдера (для КЦ из InVoice / для розницы - номер подписки из WD) : нет 3. Описание проблемы : не отключается сим меню 4. Текст сообщения на экране телефона (не путать с Tele2 тема) : Ваша заявка выполнена С уважением, Ващенко Игорь Специалист по обработке клиентских запросов, Сервисный центр клиентских б...   
991    Доброго времени суток! 0. Номер абонента : 79011770045 1. Дата и время заказа : 08.02.2023 2. Номер провайдера (для КЦ из InVoice / для розницы - номер подписки из WD) : sim меню 3. Описание проблемы : не может отключить сим меню . пробовал и через комбинацию (*152*8#) , и через само сим меню 4. Текст сообщения на экране телефона (не путать с Tele2 тема) : пишет что отключено , но после перезагрузки телефона появляется снова ПРОСЬБА ПРИ ОТВЕТЕ НА ЗАПРОС ИСПОЛЬЗЬЗОВАТЬ ФУН...   
1211                                                 Доброго времени суток! Просьба помочь в решении вопроса 0. Номер абонента : 79512699455 1. Дата и время заказа : 16.02.2023 16:53:00 2. Номер провайдера (для КЦ из InVoice / для розницы - номер подписки из WD) : сим меню 3. Описание проблемы : не отключатся 4. Текст сообщения на экране телефона (не путать с Tele2 тема) : запрос принят ICC 89701203965303292516 IMSI 250206100895546 ПРОСЬБА ПРИ ОТВЕТЕ НА ЗАПРОС ИСПОЛЬЗЬЗОВАТЬ ФУН...   
1613       Доброго времени суток. Просьба помочь в решении вопроса абонента. 0. Номер абонента : 79029095087 1. Дата и время заказа : всегда, последний раз 

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [66]:
assign_cluster(df, 'descr', ['sim меню', 'sim-меню'], exact_match=False)

theme  \
0                                                       Жалоба абонента  TT20595877   
66                                                      Жалоба абонента  TT20620268   
71                                                      Жалоба абонента  TT20622080   
149                                                               Жалоба TT20650547   
467                                                     Жалоба абонента  TT20762142   
545                                                     Жалоба абонента  TT20783304   
571                                                     Жалоба абонента  TT20783304   
979                                                               Жалоба TT20903581   
1169                                                    Жалоба абонента  TT20971228   
1358                                                              Жалоба TT21034725   
1667                                                     Жалоба абонента TT21153420   
1948                                                    Жалоба абонента  TT21309305   
1994                                                    Жалоба абонента  TT21324000   
2046                                                              Жалоба TT21346361   
2131                                                              Жалоба TT21383397   
2512                                                              Жалоба TT21627856   
2548                                                              Жалоба TT21652170   
2597                                                    Жалоба абонента  TT21675086   
2709                                                              Жалоба TT21757914   
3002                                                    Жалоба абонента  TT21916060   
3582                                                    Жалоба абонента  TT22252832   
3746                                                              Жалоба TT22371757   
3777                                                              Жалоба TT22399375   
3820                                                                     TT22444488   
4074                                                              Жалоба TT22664321   
4343                                                              Жалоба TT22920461   
5267                                                              Жалоба TT23631868   
5279                                                              Жалоба TT23718181   
5384                                                     Жалоба абонента TT23803051   
5397                                                              Жалоба TT23824820   
5436                                                    Жалоба абонента  TT23870292   
5703                                                              Жалоба TT24077235   
5854                                                             Жалоба  TT24256630   
5936                                                    Жалоба абонента  TT24369203   
6348                                                              Жалоба TT24832893   
7111                                                    Жалоба абонента  TT25572510   
7311                                                    Жалоба абонента  TT25832612   
7580                                                    Жалоба абонента  TT26043152   
7608                                                              Жалоба TT26043152   
7619                                                    Жалоба абонента  TT26066244   
7885                                                    Жалоба абонента  TT26386348   
8145   FW: №3696-02/56 от 23.04.2024: О направлении запроса по обращению TT26635779   
8255                                                    Жалоба абонента  TT26787562   
8404                                                                     TT26970077   
8405                                                    Жалоба абонента  TT26978614   
8423                                                              Жалоба TT2

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [73]:
assign_cluster(df, 'descr', ['Просим проверить корректность списаний и рассмотреть вопрос о компенсации!'], exact_match=False)

Output hidden; open in https://colab.research.google.com to view.

In [75]:
df.cluster.value_counts()

# к сожалению, это реальная картинка! жалобы практически идентичные, все пойдут в один кластер.

cluster
1    3971
9     945
4     371
5     330
8      89
2      82
Name: count, dtype: int64

In [77]:
assign_cluster(df, 'theme', ['есим', 'esim'], exact_match=False)

theme  \
49                                                                                    Представление кода активации esim в формате, поддерживаемом часами   
63                                                                                                                                                  eSIM   
186                                                                                                               Request for eSIM technology discussion   
217                                                                                                        TT№87863606 - не загрузить eSIM на устройство   
361                                                                                          TT№87867778 — А2: Недоступен заказ eSIM на всех платформах.   
548                                                                                                               TT№87870651 - Сбой при активации еСИМ.   
614                                                                                                     Проблемы установки профилей eSim Тинькофф Мобайл   
647                                                                                                                    TT№87872833 - Сбой активации eSIM   
732                                                                                                     TT№87874913 — Ticket: Проблемы с активацией eSim   
770                                                                                                                                        esim подписки   
776                                                                                                               TT№87875589 Проблемы с активацией eSim   
785                                                                                                                                Ошибка активации esim   
811                                                                                                                    TT№87875493 - сбой активации еСИМ   
826                                                                                                                    TT№87875776 — Восстановление esim   
970                                                                                          TT№87879878 — Ticket: Тестирование eSIM на аппаратах iPhone   
972                                                                                           TT№87880017 — Ticket: Ошибка при установки eSIM 9957477659   
992                                                                                                              TT№87878270 - Ошибка при активации еСИМ   
1018                                                                                                             TT№87880240 - Ошибка при активации еСИМ   
1032                                                                                 [Tinkoff: 9939951] Проблемы установки профилей eSim Тинькофф Мобайл   
1152                                                                                                                               Ошибка активации esim   
1212                                                                                                                               Ошибка активации esim   
1368                                                                                                                 TT№87888501 - Ошибка установки еСИМ   
1432                                                                                                                  TT№87890575 -  сбой активации еСИМ   
1456                                                                                                                 TT№87890146 - Ошибка установки еСИМ   
1542                                                                                                                 TT№87892798 - Ошибка установки еСИМ   
1581                                                                                       

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [82]:
assign_cluster(df, 'descr', ['есим', 'esim', 'е-сим', 'e-sim'], exact_match=False,
               exclude_keywords = ['принудительно сброс в available', 'направить отчет', 'Я нахожусь в отпуске по',
                                   'yesim', 'доступ в веб интерфейс платформы'])

theme  \
88                                                                                              TT№87861926   
171                                                                                            Not Provided   
241                                                            TT№87865099 — Персональное обслуживание в КЦ   
288                                                                                            Not Provided   
500                                                                                             TT№87870918   
778                                                                                             TT№87874416   
779                                                                                             TT№87875298   
791                                                                                             TT№87875324   
843                                                                                             TT№87876021   
844                                                                                             TT№87876312   
851                                                                                             TT№87872964   
913                                                                                             TT№87878270   
916                                                                                             TT№87878859   
948                                                                                             TT№87878919   
952                                                                                             TT№87878919   
953                                                                                             TT№87879356   
959                                                                                             TT№87879292   
960                                                                                             TT№87878988   
1035                                                                                            TT№87881048   
1041                                                                                            TT№87881090   
1061                                                               TT№87881574 - Проблемы с установкой еSIM   
1100                                                                                            TT№87882302   
1151                                                                                            TT№87883214   
1168                                                           TT№87883317 — Персональное обслуживание в КЦ   
1203                                                                                            TT№87884938   
1232                                                                                            TT№87885606   
1233                                                                                            TT№87885236   
1234                                                                                            TT№87885556   
1239                                                                                            TT№87884988   
1247                                                                                            TT№87886076   
1350                                                                                            TT№87887225   
1632                                                                                            TT№87894425   
1668                                                           TT№87896235 — Персональное обслуживание в КЦ   
1718                                                                                            TT№87897330   
1784                                                                                            TT№87898892   
1805                                                           TT№87899693 — Персональное обслуживание в К

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [85]:
assign_cluster(df, 'descr', ['списание'], exact_match=False)

theme  topic  \
3238                           Жалоба TT22060807      2   
3337  Жалоба абонента +375333219502: Семья здесь      4   
3466                         жалоба 375297816856      4   
7607          семья здесь-обращение 375297164737      4   
8995                          Интерфейс работает      2   
9188                          Интерфейс работает      2   
9533                          Интерфейс работает      2   
9618                          Интерфейс работает      2   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 descr  \
3238                                          Доброго день! Просьба рассмотреть вопрос абонента. 1. Номер абонента : 79029651673 2. Дата и время : 15:49 04.06.2023 3. Номер USSD : набора комбинации не было 4. Ответ сети : ответ системы не поступал 5. Описание проблемы : После смены тарифного плана, с блэк на МО+ не произошла смена названия сети, сеть осталась на Tele2Black 6. Номер КП : 7. Сумма потраченных средств : списание не было 8. Сумма компенсации : не было 9. КП не ответил : не было 10....   
3337                                                    Добрый день. Поступило обращение абонента + 375333219502 с несогласием со списанием д/с за услугу «Семья здесь». Прошу проверить, были ли запросы на определение местоположения с этого номера и были ли добавлены члены семьи в приложение для отслеживания. Спасибо. С уважением, Ирина Марачковская Специалист по маркетингу Отдел базовых сервисов и бизнес-продуктов Управление продуктового маркетинга и стратегии СООО «Мобильные ТелеСистемы» _____...   
3466                                             Добрый день. Поступило обращение абонента + 375297816856 с несогласием со списанием д/с за услугу «Семья здесь». Прошу проверить, были ли запросы на определение местоположения с этого номера и были ли добавлены члены семьи в приложение для отслеживания. Спасибо. С уважением, Ирина Марачковская Специалист по маркетингу Отдел базовых сервисов и бизнес-продуктов Управление продуктового маркетинга и стратегии СООО «Мобильные ТелеСистемы» ____________...   
7607                             Добрый день. Поступила жалоба абонента + 375297164737 на необоснованное списание д/с за услугу Семья здесь (03.02.2023-25.03.2024), абонент утверждает что не подключал и не пользовался услугой. Прошу вас проверить, осуществлялась ли регистрация в приложении, отправлялись ли запросы на определение местоположения члена семьи. Спасибо. С уважением, Ирина Марачковская Специалист по маркетингу Отдел базовых сервисов и бизнес-продуктов Управление продуктового маркетин...   
8995      Здравствуйте!Вы получили это письмо, так как подписаны на его рассылку. Канал предоставления ответа клиенту (при необходимости) (Эл. почта или WhatsApp): 87052052426 ватцап Номер телефона, на котором подключена услуга: 87052052426 Номер абонента, с которого поступил вызов (канал – голос/WA): 87052052426 Описание вопроса/проблемы: не происходит списание Название услуги: КаР-Тел - «Удача» - - - Пожалуйста, не отвечайте на это письмо, это автоматическое уведомление. Информация, представл...   
9188      Здравствуйте!Вы получили это письмо, так как подписаны на его рассылку. Канал предоставления ответа клиенту (при необходимости) (Эл. почта или WhatsApp): 87017565590 вотцап Номер телефона, на котором подключена услуга: 87082783158 Номер абонента, с которого поступил вызов (канал – голос/WA): 87082783158 Описание вопроса/проблемы: абонент утверждает что приходят смс о покупке билета и списание идет,но услуга не подключена Название услуги: Тele2 - «Твоя Удача» - 

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [86]:
assign_cluster(df, 'theme', ['плановые'], exact_match=False)

theme  topic  \
3607                             RE: Плановые работы на 27.06.2023      0   
3696  RE: Плановые работы на 05.07.2023 локальное время по Бишкеку      0   
4700                   Re: [Ticket#10309258] Плановые работы Теле2      1   
5457  RE: Плановые работы на 14.11.2023 локальное время по Бишкеку      0   
5723  RE: Плановые работы на 21.11.2023 локальное время по Бишкеку      0   
5767  RE: Плановые работы на 28.11.2023 локальное время по Бишкеку      0   
5865  FW: Плановые работы на 05.12.2023 локальное время по Бишкеку      0   
6014  FW: Плановые работы на 14.12.2023 локальное время по Бишкеку      0   
6640  RE: Плановые работы на 14.12.2023 локальное время по Бишкеку      0   
6978  RE: Плановые работы на 15.02.2024 локальное время по Бишкеку      0   
7091  RE: Плановые работы на 27.02.2024 локальное время по Бишкеку      0   
7739  RE: Плановые работы на 04.04.2024 локальное время по Бишкеку      0   
7847  FW: Плановые работы на 11.04.2024 локальное время по Бишкеку      0   
7989  RE: Плановые работы на 19.04.2024 локальное время по Бишкеку      0   
9786                            Плановые работы на RSP Consumer IM      4   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   descr  \
3607                  Добрый день, коллеги В ночь на 27.06.2023 будут проводиться работы на промышленной БД ИБС. В связи с этим в период с 01:00 до 05:30 27.06.2023 будут недоступны USSD и SMS-услуги, прием платежей, задержка в тарификации услуг, возможен дебет. Также, ввиду недоступности БД на период проведения работ, все сторонние, подключающиеся к БД ИБС, системы контент-провайдеров и дилеры, не будут иметь доступа к ней. Просим принять к сведению. С уважением, Курманбекова Айдай    
3696  Добрый день, коллеги 05.07.2023 с 01:00 до 05:30 Отделом Биллинга будут проводиться работы на промышленной БД ИБС. В связи с этим в период 05.07.2023 с 01:00 до 05:30 будут недоступны USSD и SMS-услуги, прием платежей, задержка в тарификации услуг, возможен дебет. Также, ввиду недоступности БД на период проведения работ, все сторонние системы контент-провайдеров, подключающиеся к БД ИБС, не будут иметь доступа к ней. Просим принять к сведению. С уважением, Курманбекова Айдай...   
4700                                                                Уважаемый партнер! Сотовый оператор Теле2 сообщает о необходимости проведения плановых технических работ. Работы будут проводиться 11.09.2023 в период с 23:00 до 12.09.2023 03:00 (МСК/GMT +3). В указанный промежуток времени могут наблюдаться затруднения в доставке сообщений абонентам данного оператора. С уважением, Rapporto Support Team 8 (495) 260-55-99 (круглосуточно) 8 (800) 555-08-36 (звонок по России бесплатный)   
5457                             Добрый день, коллеги В ночь на 14.11.2023 будут проводиться работы на промышленных серверах HRS (High Rating Server) и BRT (Billing Real Time). Простоя в работе сервисов не предвидится ввиду попеременного проведения работ на серверах, но возможно частичное влияние на сервисы тарификации услуг связи до 10 минут в указанном интервале времени 14.11.2023 01:00 – 07:20. Просим принять к сведению. С уважением, Курманбекова Айдай Ведущий специалист по раб...   
5723                                         Добрый день, коллеги В ночь на 21.11.2023 года с 02:00 - 05:00 часов утра, будут проводиться аварийные работы на нашей сети. Ожидается проблемы с дозвоном и отправкой смс в нашу сеть в указанном интервале времени. К сожалению, отменить или перенести данные работы невозможно. Просим принять к сведению. С уважением, Курманб

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [87]:
assign_cluster(df, 'theme', ['плановых работах'], exact_match=False)

theme  \
251                                                                          Re: [Ticket#10277533] Уведомление о плановых работах у оператора Теле 2   
315                                                                          Re: [Ticket#10277695] Уведомление о плановых работах у оператора Билайн   
323                                                                                      Re: [Ticket#10277785] Уведомление о плановых работах Билайн   
360                                                                               Re: [Ticket#10277958] Уведомление о плановых работах оператора МТС   
405                                                                           Re: [Ticket#10278282] Уведомление о плановых работах оператора Мегафон   
406                                                                           Re: [Ticket#10278276] Уведомление о плановых работах оператора Мегафон   
493                                                                           Re: [Ticket#10278672] Уведомление о плановых работах оператора Мегафон   
525                                                                         Re: [Ticket#10278856] Уведомление о плановых работах оператора (Мегафон)   
526                                                                   Re: [Ticket#10278857] Уведомление о плановых работах оператора Теле2 (февраль)   
535                                                                            Re: [Ticket#10278938] Уведомление о плановых работах оператора Билайн   
579                                                                            Re: [Ticket#10279159] Уведомление о плановых работах оператора Билайн   
581                                                                            Re: [Ticket#10279185] Уведомление о плановых работах оператора Билайн   
639                                                                               [Ticket#10279528] Уведомление о плановых работах оператора Мегафон   
641                                                                    [Ticket#10279573] Уведомление о плановых работах на платформе lk.zagruzka.com   
726                                                                   Re: [Ticket#10279786] Уведомление о плановых работах оператора Теле2 Казахстан   
761                                                                       [Ticket#10279970] Уведомление о плановых работах оператора Теле2 Казахстан   
777                                                                            [Ticket#10280028] Уведомление о плановых работах на Дата центре (ЦОД)   
795                                                                       [Ticket#10280226] Уведомление о плановых работах оператора Теле2 Казахстан   
818                                                                           Re: [Ticket#10280411] Уведомление о плановых работах оператора Мегафон   
910                                                                                [Ticket#10280824] Уведомление о плановых работах оператора Билайн   
937                                                                   Re: [Ticket#10280930] Уведомление о плановых работах оператора Теле2 Казахстан   
975                                                                                      Re: [Ticket#10281167] Уведомление о плановых работах Билайн   
976                                                                               [Ticket#10281178] Уведомление о плановых работах оператора Мегафон   
1007                                                                              [Ticket#10281369] Уведомление о плановых работах оператора Мегафон   
1120                                                                           [Ticket#10281993] Уведомление о плановых работах на Дата центре (ЦОД)   
1126                                                                                      Re: [Ticket#10282030] Уведомление о плановых работах Теле2   
1127                                   

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [91]:
assign_cluster(df, 'descr', ['плановые работы', 'плановых работ'], exact_match=False)

theme  \
543                                   FW: Профилактические работы в OOO "UMS"   
2468                           FW: Профилактические работы на стороне OOO UMS   
4022                                                           RE: Работы RSP   
4236                                                           RE: Работы RSP   
4255                                                Проведение плановых работ   
4272                                                 TT№87977668 - Работы RSP   
5243     [Ticket#10314397] Уведомление о проведении плановых работ Белтелеком   
6843                              FW: Уведомление о проведение плановых работ   
8007                                                       RE: Работы на сети   
8501  Проведением плановых работ на внутренних биллинговых системах OOO "UMS"   

      topic  \
543       0   
2468      0   
4022      1   
4236      1   
4255      1   
4272      3   
5243      1   
6843      1   
8007      1   
8501      0   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        descr  \
543                                             Коллеги, добрый день. Прошу принять к сведению информацию о плановых работах на стороне UMS. 25.01.2023 с 0:00 до 2:00 запланированы работы по обновлению программного обеспечения, в ходе которых возможны кратковременные обрывы SMPP-линков со всеми контент-провайдерами (включая платёжные системы). _ C уважением, Шишова Екатерина Менеджер по работе с партнерами A1 Systems Моб.: +7 (916) 112-70-30 E-mail: E.Shishova@a1-systems.com От: Носиро...   
2468                                        Коллеги, добрый день. Прошу принять к сведению информацию о плановых работах на стороне оператора: Сообщаем Вам, что в день празднования Рамазан Хайита (21.04.2023) в связи с увеличением нагрузки на SMS-центр планируется блокировать все SMPP-соединения с контент-провайдерами, за исключением платёжных систем. Ориентировочное время начала блокировок – 4:00. Окончание – после снижения нагрузки на SMS-центр. _ C уважением, Шишова Екатерина Менедж...   
4022  Добрый день, коллеги, какой город проведения работ? Александр Иванов Менеджер по координации плановых работ ЕЦУС Технический блок - Направление оперативно-технического управления координации плановых работ ЕЦУС Запад -----Original Message----- From: rsp_support@a1-systems.com [mailto:rsp_support@a1-systems.com] Sent: Friday, July 21, 2023 1:32 PM To: Координация плановых работ Запад &lt;gnocwest_works@MegaFon.ru&gt; Координация плановых работ (GNOC) &lt;gnoc_works@megafon.ru&gt; ...   
4236                       #ИМЯ?;gnocwest_sp@MegaFon.ru&gt; ДИ Александр Иванов -----Original Message----- From: rsp_support@a1-systems.com [mailto:rsp_support@a1-systems.com] Sent: Tuesday, August 8, 2023 12:48 PM To: Координация плановых работ (GNOC) &lt;gnoc_works@megafon.ru&gt; Координация плановых работ Запад &lt;gnocwest_works@MegaFon.ru&gt; Cc: Мартынова Ирина (NW) &lt;irina.martynova@MegaFon.ru&gt; Абышев Георгий (HQ) &lt;georgy.abyshev@MegaFon.ru&gt; Курицын Дмитрий (HQ) &lt;d...   
4255                                            Здравствуйте, коллеги! Запланированы плановые работы, прошу учесть. Планируемые/ возможные изменения и последствия Начало работ: Дата окончания (планируемая): Плановые работы , В связи с проведением плановых работ ОЭОС VAS 10.08.2023 с 01:00-06:00, возможны затруднения с входящими и исходящими SMS по всей сети до 60 мин, в указанном интервале времени. Затруднения , 10.08.2023 01:00:00 10.08.2023 06:00:00 С уважением, Закирова Жанара Специ...   
4272         Коллеги, добрый ден

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [94]:
assign_cluster(df, 'descr', ['сбой'], exact_match=False)

theme  \
5                                              Re: [Ticket#10276498] Уведомление.Сбой на стороне оператора Теле2-Казахстан (01.01.23 14:19-15:03)   
318                                                                                       [Ticket#10277705] Уведомление о сбое у оператора Билайн   
331                                                                                        Re: [Ticket#10277833] Уведомление о сбое оператора МТС   
333                                                                                        Re: [Ticket#10277844] Уведомление о сбое оператора МТС   
519                                                                               [Ticket#10278823] Уведомление о сбое у оператора Глобал Телеком   
532                                                                                           Re: [Ticket#10278913] Сбой на стороне оператора МТС   
557                                                                                 Re: [Ticket#10279037] Уведомление о сбое оператора Таттелеком   
565                                                                  Re: [Ticket#10279071] Уведомление.Сбой на стороне оператора МТС (25.01.2023)   
574                                                                                            Re: [Ticket#10279129] Уведомление о сбое Microsoft   
582                                                                        [Ticket#10279189] Уведомление о сбое на стороне оператора КТК -Телеком   
1048                                                                               Re: [Ticket#10281605] Уведомление о сбое на стороне операторов   
1050                                                                     Re: [Ticket#10281637] Уведомление о сбое на стороне оператора Ростелеком   
1052                                                                      Re: [Ticket#10281656] Уведомление о сбое на стороне оператора К-Телеком   
1101                                                                                   [Ticket#10281937] Уведомление о сбое оператора Сим Телеком   
1280                                                                                           [Ticket#10282932] Уведомление о сбое оператора МТС   
1291                                                                                         [Ticket#10283038] Уведомление о сбое оператора Теле2   
1367                                                                    Re: [Ticket#10283519] Уведомление о сбое на стороне оператора Воентелеком   
1374                                                                  Re: [Ticket#10283571] Уведомление о сбое оператора КТК-Телеком (24.02.2023)   
1586                                                                                    [Ticket#10284708] Уведомление о сбое оператора Таттелеком   
1954                                                                                       Re: [Ticket#10287367] Уведомление о сбое оператора МТТ   
2005                                                                               [Ticket#10287688] Уведомление о сбое оператора Тинькофф Мобайл   
2192                                                                               Re: [Ticket#10289027] Уведомление о сбое оператора Воентелеком   
2200                                                                                     Re: [Ticket#10289115] Уведомление о сбое оператора Мотив   
2203                                                                            Re: [Ticket#10289184] Уведомление о сбое оператора Феникс -Херсон   
2239                                                                                        [Ticket#10289620] Уведомление о сбое оператора Спринт   
2249                                                           Re: [Ticket#10289723] Уведомление о сбое оператора Газпромбанк Мобайл (07.04.2023)   
2262                                                                                        [Ticket#10289872] Уведомл

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [96]:
assign_cluster(df, 'theme', ['сбое оператор', 'сбое на стороне оператора'], exact_match=False)

theme  \
540                                     [Ticket#10278969] Уведомление о сбое оператора FlashingCall   
1019                         [Ticket#10281418] Уведомление о сбое оператора FlashingCallи VoiceCode   
1071                                    [Ticket#10281745] Уведомление о сбое оператора FlashingCall   
1369      Re: [Ticket#10283535] Уведомление о сбое на стороне оператора Воентелеком -восстановление   
2542  Re: [Ticket#10292767] Уведомление о сбое на стороне оператора Тинькофф Мобайл -восстановление   
2545  Re: [Ticket#10292773] Уведомление о сбое на стороне оператора Тинькофф Мобайл -восстановление   
3493                     [Ticket#10300004] Уведомление о сбое операторов международного направления   

      topic  \
540       1   
1019      1   
1071      1   
1369      1   
2542      1   
2545      1   
3493      1   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                          descr  \
540                           Уважаемый партнер! Данная информация будет вам полезна, если вы используете сервис звонков FlashingCall. Уведомляем Вас, что на сети предоставления услуг FlashingCall могут наблюдаться затруднения в доставке звонков абонентам. Информации от оператора о причинах и сроках устранения ограничений на данный момент не поступило -- С уважением, Отдел технической поддержки АО "Загрузка" help@zagruzka.com 8 (495) 287-03-28 (круглосуточно)   
1019  Уважаемый партнер! Данная информация будет вам полезна, если вы используете сервис звонков FlashingCall и VoiceCode. Уведомляем Вас, что на сети предоставления услуг FlashingCall и VoiceCode могут наблюдаться затруднения в доставке звонков абонентам. Информации от оператора о причинах и сроках устранения ограничений на данный момент не поступило -- С уважением, Отдел технической поддержки АО "Загрузка" help@zagruzka.com 8 (495) 287-03-28 (круглосуточно)   
1071                         Уважаемый партнер! Данная информация будет вам полезна, если вы используете сервис звонков FlashingCall. Уведомляем Вас, что на сети предоставления услуг FlashingCall могут наблюдаться затруднения в доставке звонков абонентам. Информации от оператора о причинах и сроках устранения ограничений на данный момент не поступило. -- С уважением, Отдел технической поддержки АО "Загрузка" help@zagruzka.com 8 (495) 287-03-28 (круглосуточно)   
1369                                                                                                                                                                                    Уважаемый партнёр! Фиксируем восстановление сервиса доставки сообщений абонентам сотового оператора "Воентелеком". При этом информации об устранении сбоя от оператора на данный момент не поступало. -- Отдел технической поддержки АО "Загрузка" help@zagruzka.com +7 (495) 287-03-28   
2542                                                                                                 Фиксируем восстановление сервиса доставки сообщений абонентам сотового оператора "Тинькофф Мобайл". Проблемы наблюдались 12.04.2023 в период с 20:44 до 21:11 (МСК / GMT+3) При этом информации об устранении сбоя от оператора на данный момент не поступало. -- Rapporto Support Team 8 (495) 565-36-08 (круглосуточно) 8 (800) 555-08-36 (звонок по России бесплатный)    
2545                                                                                 Уважаемый партнёр! Фиксируем восстановление сервиса доставки сообщений абонентам сотового оператора "Тинькофф Мобайл". Проблемы наблюдались 25.04.23 в период с 21:34 до 21:52 (МСК / GMT+3) При этом информации об устранении сбоя от оператора на данный момент не 

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [100]:
assign_cluster(df, 'theme', ['reminder'], exact_match=False)

theme  topic  \
16                                 Sim reminder      9   
2222  Жалоба TT21439715 отключение Sim-reminder      9   
3274           Абонент отключен от SIM reminder      3   

                                                                                                                                                                                                                                                                                                                                                     descr  \
16                                                                                                                                                                                                                         Здравствуете, Прошу отключить сим ремайндер на следующем номере: 994512339755 С уважением, Камила. Получите Outlook для Android   
2222  Добрый день! Номер абонента: 79018897034 Прошу отправить команду на отключение Sim-reminder и также просим внести абонента в ЧС по Tele2-тема. С уважением, Чернейкин Дмитрий Специалист по обработке клиентских запросов Сервисный центр клиентских бэк-офисных операций Tele2 Россия Саранск Васенко, 9 430031, Саранск, Россия Моб. +79520714865    
3274                                                                                                                                                                                                                                                                      Здравствуйте коллеги! Отключите пожалуйста сим ремайндер на номере: 994514461977   

           sender_name  
16    Kamila Movlanova  
2222   content_problem  
3274   Nazrin Guliyeva

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [102]:
assign_cluster(df, 'descr', ['reminder', 'ремайндер', 'меню'], exact_match=False)

theme  topic  \
33                                             Отключить сим ремайндер      3   
91                                         Жалоба абонента  TT20637973      9   
92                                         Жалоба абонента  TT20637973      9   
93                                                   Жалоба TT20632330      9   
102                                                  Жалоба TT20637533      9   
166   На Вашу роль зарегистрировано обращение № 34503264. Приоритет: 4      6   
212                                            Отключить сим ремайндер      3   
308                                        Жалоба абонента  TT20714166      2   
382                                            Отключить сим ремайндер      3   
485                                            Отключить сим ремайндер      3   
569                                            Отключить сим ремайндер      3   
735                                                  Жалоба TT20838001      9   
974                                                  Жалоба TT20911032      9   
1221                                                 Жалоба TT20989995      9   
1229                                       Жалоба абонента  TT20976490      2   
1254                                       Жалоба абонента  TT20997742      9   
1255                                       Жалоба абонента  TT20997742      9   
1360                                                 Жалоба TT21032282      9   
1363                                           Отключить сим ремайндер      3   
1575                                                 Жалоба TT21124982      9   
1662                                       Жалоба абонента  TT21161156      9   
1710                                           Отключить сим ремайндер      3   
1711                                           Отключить сим ремайндер      3   
1749                                           отключите сим ремайндер      3   
1761                                           Отключить сим ремайндер      3   
1822                                       Жалоба абонента  TT21232582      9   
1963                                                 Жалоба TT21304148      9   
2053                                        Жалоба абонента TT21353512      9   
2059                                           отключить сим ремайндер      3   
2073                                                 Жалоба TT21357959      9   
2077                                           отключить сим ремайндер      3   
2112                                                    FW: TT21367483      9   
2148                                                 Жалоба TT21397014      9   
2293                                           отключить сим ремайндер      3   
2403                                           отключить сим ремайндер      3   
2427                                           отключить сим ремайндер      3   
2443                                           Отключить сим ремайндер      3   
2551                                           отключить сим ремайндер      3   
2730                                           отключить сим ремайндер      3   
2748                                 отключить сим ремайндер на номере      3   
2772                                           отключить сим ремайндер      3   
2803                                отключить сим ремайндер на номерах      3   
2827                                           отключить сим ремайндер      3   
2860                                                 Жалоба TT21841987      9   
2909                                           отключить сим ремайндер      3   
2944                                           Отключить сим ремайндер      3   
3160                                           отключить сим ремайндер      3   
3210                                           отключить сим ремайндер      3   
3272                                                 Жалоба TT22095178      9   
3464           

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [112]:
assign_cluster(df, 'theme', 'UMS - отключенные номера', exact_match=False)

theme  topic  \
7728   UMS - отключенные номера за 02-04-2024      5   
7729   UMS - отключенные номера за 02-04-2024      5   
7741   UMS - отключенные номера за 03-04-2024      5   
7750   UMS - отключенные номера за 04-04-2024      5   
7770   UMS - отключенные номера за 05-04-2024      5   
7791   UMS - отключенные номера за 06-04-2024      5   
7798   UMS - отключенные номера за 07-04-2024      5   
7815   UMS - отключенные номера за 08-04-2024      5   
7840   UMS - отключенные номера за 09-04-2024      5   
7854   UMS - отключенные номера за 10-04-2024      5   
7862   UMS - отключенные номера за 11-04-2024      5   
7873   UMS - отключенные номера за 12-04-2024      5   
7887   UMS - отключенные номера за 13-04-2024      5   
7897   UMS - отключенные номера за 14-04-2024      5   
7901   UMS - отключенные номера за 15-04-2024      5   
7931   UMS - отключенные номера за 16-04-2024      5   
7943   UMS - отключенные номера за 17-04-2024      5   
7973   UMS - отключенные номера за 18-04-2024      5   
7997   UMS - отключенные номера за 19-04-2024      5   
8011   UMS - отключенные номера за 20-04-2024      5   
8021   UMS - отключенные номера за 21-04-2024      5   
8034   UMS - отключенные номера за 22-04-2024      5   
8055   UMS - отключенные номера за 23-04-2024      5   
8081   UMS - отключенные номера за 24-04-2024      5   
8099   UMS - отключенные номера за 25-04-2024      5   
8112   UMS - отключенные номера за 26-04-2024      5   
8132   UMS - отключенные номера за 27-04-2024      5   
8151   UMS - отключенные номера за 28-04-2024      5   
8159   UMS - отключенные номера за 29-04-2024      5   
8175   UMS - отключенные номера за 30-04-2024      5   
8198   UMS - отключенные номера за 01-05-2024      5   
8218   UMS - отключенные номера за 02-05-2024      5   
8236   UMS - отключенные номера за 03-05-2024      5   
8257   UMS - отключенные номера за 04-05-2024      5   
8263   UMS - отключенные номера за 05-05-2024      5   
8272   UMS - отключенные номера за 06-05-2024      5   
8284   UMS - отключенные номера за 07-05-2024      5   
8310   UMS - отключенные номера за 08-05-2024      5   
8318   UMS - отключенные номера за 09-05-2024      5   
8330   UMS - отключенные номера за 10-05-2024      5   
8342   UMS - отключенные номера за 11-05-2024      5   
8351   UMS - отключенные номера за 12-05-2024      5   
8364   UMS - отключенные номера за 13-05-2024      5   
8384   UMS - отключенные номера за 14-05-2024      5   
8403   UMS - отключенные номера за 15-05-2024      5   
8430   UMS - отключенные номера за 16-05-2024      5   
8444   UMS - отключенные номера за 17-05-2024      5   
8464   UMS - отключенные номера за 18-05-2024      5   
8475   UMS - отключенные номера за 19-05-2024      5   
8478   UMS - отключенные номера за 20-05-2024      5   
8497   UMS - отключенные номера за 21-05-2024      5   
8517   UMS - отключенные номера за 22-05-2024      5   
8528   UMS - отключенные номера за 23-05-2024      5   
8559   UMS - отключенные номера за 24-05-2024      5   
8577   UMS - отключенные номера за 25-05-2024      5   
8593   UMS - отключенные номера за 26-05-2024      5   
8597   UMS - отключенные номера за 27-05-2024      5   
8605   UMS - отключенные номера за 28-05-2024      5   
8623   UMS - отключенные номера за 29-05-2024      5   
8637   UMS - отключенные номера за 30-05-2024      5   
8655   UMS - отключенные номера за 31-05-2024      5   
8667   UMS - отключенные номера за 01-06-2024      5   
8680   UMS - отключенные номера за 02-06-2024      5   
8689   UMS - отключенные номера за 03-06-2024      5   
8704   UMS - отключенные номера за 04-06-2024      5   
8722   UMS - отключенные номера за 05-06-2024      5   
8748   UMS - отключенные номера за 06-06-2024      5   
8764   UMS - отключенные номера за 07-06-2024      5   
8776   UMS - отключенные номера за 08-06-2024      5   
8787   UMS - отключенные номера за 09-06-2024      5   
8795   UMS - отключенные номера за 10-06-2024      5   
8812   U

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [122]:
assign_cluster(df, 'descr', [ 'отключ'], exact_match=False, exclude_keywords=['списыва', 'списание', 'вернуть деньги', 'возврат средств',
                                                                              'информация от СП Яхонт','Tele2Black отключается автоматически',
                                                                              'отображается баланс на экране телефона', 'всплывающее окно', ' ЧС'])

theme  topic  \
15                                        Not Provided      3   
202                        Жалоба абонента  TT20671256      9   
218                                  Жалоба TT20681473      2   
247                        запрос из Билайн 9057121873      6   
286                                  Жалоба TT20707491      2   
310                              инцидент_375336441504      4   
316                              инцидент_375295395796      4   
317                        Жалоба абонента  TT20715949      2   
352                        Жалоба абонента  TT20724991      2   
369                                  Жалоба TT20728297      2   
385                              инцидент_375297103864      4   
444                        Жалоба абонента  TT20753784      2   
490                                  Жалоба TT20770110      2   
577                                  Жалоба TT20791921      2   
597                                  Жалоба TT20799258      2   
714                         Жалоба абонента TT20829771      9   
765                        Жалоба абонента  TT20839891      2   
802                                        Re: Контент      9   
803                                  Жалоба TT20850348      9   
807                                  Жалоба TT20857570      2   
836                        Жалоба абонента  TT20850960      9   
862                        Жалоба абонента  TT20871596      2   
967           Запрос на изменение параметров https OTA      2   
969                         Жалоба абонента TT20907364      2   
973                                  Жалоба TT20910785      2   
980                               УЗ StreamFirstClient      3   
1005                           Живой баланс TT20920795      2   
1028                                        TT20922583      2   
1072                                 Жалоба TT20939666      2   
1161                                      Not Provided      3   
1162   Запрос в рамках письменной претензии TT20803784      9   
1163   Запрос в рамках письменной претензии TT20803784      9   
1165                                 Жалоба TT20963457      2   
1230                       Жалоба абонента  TT20979602      2   
1261                                 Жалоба TT21000594      2   
1275                       Жалоба абонента  TT21007401      2   
1283                                Жалоба  TT21011237      2   
1304                             инцидент_375297556710      4   
1329        Жалоба TT21026642 Теле2-Тема черный список      9   
1381                                 Жалоба TT21046231      2   
1399                                 Жалоба TT21052908      2   
1404                       Жалоба абонента  TT21055308      2   
1489                                 Жалоба TT21092741      2   
1493                                      Not Provided      3   
1517                           Живой баланс TT21086365      2   
1521                       Жалоба абонента  TT21105616      2   
1536                                      Not Provided      3   
1571                       Жалоба абонента  TT21124929      2   
1574                                Жалоба  TT21126339      2   
1576                                 Жалоба TT21126062      2   
1609                                           Контент      6   
1630                                 Жалоба TT21140451      2   
1690                                 Жалоба TT21168530      2   
1748                             инцидент_375292858278      4   
1755                           отключить сим ремайндер      3   
1875                       Жалоба абонента  TT21261947      2   
1876                       Жалоба абонента  TT21264256      2   
1881                                        TT21268023      2   
1889                                 Жалоба TT21275089      2   
1891                               375259088698  99993      5   
1942                                 Жалоба TT21302795      2   
1972               

Dropdown(description='Номер кластера:', options=(1, 2, 3, 4, 5, 6, 7, 8, 9, 10), value=1)

Button(description='Присвоить кластер', style=ButtonStyle())

In [127]:
df.to_csv('razmetka_wrk.csv')